In [ ]:
import sys
from pathlib import Path
import numpy as np
from scipy.interpolate import griddata
import matplotlib.pyplot as plt
import laspy

triskele_path = Path('../triskele/python/')
sys.path.append(str(triskele_path.resolve()))
import triskele

figsize = np.array((16, 3)) * 1.5

# Setup

## Load LiDAR data

In [ ]:
def find_las(path):
    path = Path(path)
    las = list()
    
    if path.is_dir():
        for child in path.iterdir():
            las.extend(find_las(child))
    
    if path.is_file() and path.suffix == '.las':
        las.append(path)
    
    return las

In [ ]:
def auto_filter(data, treshold=.5):
    tresholds = np.percentile(data, [treshold, 100 - treshold])

    data[data < tresholds[0]] = tresholds[0]
    data[data > tresholds[1]] = tresholds[1]

In [ ]:
def bulk_load(path, name=None):
    data = {'file': path, 'name': name}

    attributes = ['x', 'y', 'z', 'intensity', 'num_returns']#, 'scan_angle_rank', 'pt_src_id', 'gps_time']
    for a in attributes:
        data[a] = list()
        
    print('Load data...')
    for f in find_las(path):
        print('{}: '.format(f), end='')
        infile = laspy.file.File(f)
        for i, a in enumerate(attributes):
            print('\r {}: [{:3d}%]'.format(f, int(i/len(attributes) * 100)), end='')
            data[a].extend(getattr(infile, a))
        infile.close()
        print('\r {}: [Done]'.format(f))

    
    print('Create matrices...', end='')
    for i, a in enumerate(attributes):
        print('\rCreate matrices: [{:3d}%]'.format(int(i/len(attributes) * 100)), end='')
        data[a] = np.array(data[a])
    print('\rCreate matrices: [Done]')
        
    print('Filter data...', end='')
    for i, a in enumerate(attributes):
        print('\rFilter data: [{:3d}%]'.format(int(i/len(attributes) * 100)), end='')
        if a == 'x' or a == 'y':
            continue
        auto_filter(data[a])
    print('\rFilter data: [Done]')

    return data

In [ ]:
C1 = bulk_load('../Data/lidar/C1/272056_3289689.las', 'C1')
#C2 = bulk_load('../Data/lidar/C2/', 'C2')
#C3 = bulk_load('../Data/lidar/C3/', 'C3')
#C123 = bulk_load('../Data/lidar/', 'C123') # Todo: Copy C1 C2 C3

## Define raster method

In [ ]:
resolution = 0.5

spatial_data = np.array((C1['x'], C1['y'], C1['z'])).T

bins = np.rint((spatial_data.max(axis=0) - spatial_data.min(axis=0)) / resolution).astype(int)
display(bins)

In [ ]:
voxels_histo, edges = np.histogramdd(spatial_data, bins=bins)
voxels_histo = voxels_histo.astype(np.float32)
voxels_histo.shape, voxels_histo.dtype

In [ ]:
voxels_histo_i, edges = np.histogramdd(spatial_data, bins=bins, weights=C1['intensity'])
voxels_histo_i = voxels_histo_i.astype(np.float32)
voxels_histo_i.shape

In [ ]:
layers = voxels_histo.shape[2]

plt.figure(figsize=figsize * np.array((1, layers)))

for i in range(layers):
    plt.subplot(layers, 1, i+1)
    plt.title('Layer {}'.format(i))
    plt.imshow(voxels_histo_i.T[i] / voxels_histo.T[i], origin='lower')
plt.show()

In [ ]:
plt.imsave('../Res/voxel_layer', voxels_histo.T[0], origin='lower')

## Create voxels and flatten raster

In [ ]:
layers = voxels_histo.shape[2]

raster = np.zeros_like(voxels_histo.T[0])
raster[:] = np.nan

voxels = (voxels_histo_i / voxels_histo).T

for i in reversed(range(layers)):
    nan_filter = np.isnan(raster)
    raster[nan_filter] = voxels[i][nan_filter]

raster

In [ ]:
del voxels_histo, voxels_histo_i

In [ ]:
plt.figure(figsize=figsize)
plt.imshow(raster, origin='lower')
plt.show()
plt.imsave('../Res/voxel_raster_i_0_5.png', raster, origin='lower')

## Interpolate NoData

In [ ]:
griddata

In [ ]:
nan_filter = np.isnan(raster)
val_filter = np.logical_not(nan_filter)
coords = np.argwhere(val_filter)
values = raster[val_filter]
grid   = np.argwhere(nan_filter)

In [ ]:
interpol_values_linear  = griddata(coords, values, grid, method='linear')
interpol_values_cubic   = griddata(coords, values, grid, method='cubic')
interpol_values_nearest = griddata(coords, values, grid, method='nearest')

raster_interpol_linear  = raster.copy()
raster_interpol_cubic   = raster.copy()
raster_interpol_nearest = raster.copy()

raster_interpol_linear[nan_filter]  = interpol_values_linear
raster_interpol_cubic[nan_filter]   = interpol_values_cubic
raster_interpol_nearest[nan_filter] = interpol_values_nearest

In [ ]:
plt.figure(figsize=figsize)
plt.imshow(raster_interpol_linear, origin='lower')
plt.show()
plt.imsave('../Res/voxel_raster_interpol_tmp_i_0_5.png', raster_interpol_linear, origin='lower')

## Why do we have high values there?

In [ ]:
raster_interpol_nearest.max(), raster_interpol_linear.max()

In [ ]:
raster_interpol_nearest.min(), raster_interpol_linear.min()

In [ ]:
raster_interpol_linear[raster_interpol_linear > 1e6] = 0

In [ ]:
plt.figure(figsize=figsize)
plt.imshow((raster_interpol_linear - raster_interpol_nearest))
plt.colorbar()
plt.show()
plt.imsave('../Res/diff_interpol.png', raster_interpol_linear - raster_interpol_nearest, origin='lower')

In [ ]:
(raster_interpol_linear - raster_interpol_nearest).max()

In [ ]:
raster_interpol_cubic[np.isnan(raster_interpol_cubic)] = np.nanargmin(raster_interpol_cubic)
raster_interpol_linear[np.isnan(raster_interpol_linear)] = np.nanargmin(raster_interpol_linear)

In [ ]:
#plt.hist(raster_interpol_cubic.reshape(-1), bins=100, label='cubic',log=True)
plt.hist(raster_interpol_linear[raster_interpol_linear < 1e6].reshape(-1), 100, label='linear',log=False)
plt.hist(raster_interpol_nearest.reshape(-1), 100, label='nearest',log=False, alpha=.8)
plt.legend()
plt.show()

In [ ]:
np.isnan(raster_interpol_nearest).sum()

## Function 

In [ ]:
import importlib
sys.path.append("..")
import rasterizer
importlib.reload(rasterizer)

In [ ]:
myraster = rasterizer.rasterize(spatial_data, C1['intensity'], 1.)

In [ ]:
myraster_r = rasterizer.rasterize(spatial_data, C1['intensity'], 1., reverse_alt=True)

In [ ]:
plt.imsave('../Res/myrstr.png', myraster, origin='upper')

In [ ]:
plt.imsave('../Res/myrstr_r.png', myraster_r, origin='upper')

In [ ]:
mid_layer = myraster - myraster_r

In [ ]:
plt.imsave('../Res/myrstr_layer_1.png', mid_layer, origin='upper')

# TMP

In [ ]:
dfc_c1 = triskele.read('../Data/phase1_rasters/Intensity_C1/UH17_GI1F051_TR.tif')
auto_filter(dfc_c1)

In [ ]:
plt.imshow(dfc_c1)
plt.show()
plt.imsave('../Res/dfc_c1.png', dfc_c1)

In [ ]:
def rasterize_cache(spatial, values, resolution=1., method='linear', reverse_alt=False, cache_dir='/tmp'):
    """Cache layer for rasterize"""
    
    cache_dir = Path(cache_dir)
    name = '{}_{}_{}_{}{}'.format(data['name'], field, str(resolution).replace('.', '_'), method,
                                  '_reversed' if reverse_alt else '')
    png_file = cache_dir.joinpath(Path(name + '.png'))
    tif_file = cache_dir.joinpath(Path(name + '.tif'))
    
    if tif_file.exists() :
        print ('WARNING: Loading cached result {}'.format(tif_file))
        raster = triskele.read(tif_file)
    else:         
        raster = rasterizer.rasterize(spatial, values, resolution, method, reverse_alt)
        triskele.write(tif_file, raster)
        plt.imsave(png_file, raster)
        
    return raster

rasterize_cache(spatial_data, C1['z'], 10, cache_dir='../Res/TMP')

In [ ]:
td = Path(Path('/tmp'))
tf = Path('test.png')
td.joinpath(tf).j